# Imports

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

from sklearn.linear_model import LinearRegression, Lasso
from sklearn.multioutput import MultiOutputRegressor
from sklearn.model_selection import train_test_split, KFold
from sklearn import metrics
import statsmodels.api as sm

from sklearn.neighbors import KNeighborsRegressor
from sklearn.model_selection import train_test_split, cross_val_score
from sklearn.preprocessing import StandardScaler, PolynomialFeatures

from sklearn.tree import DecisionTreeRegressor, plot_tree
from sklearn.ensemble import BaggingRegressor
from sklearn.model_selection import GridSearchCV, RandomizedSearchCV

from sklearn.ensemble import VotingRegressor

from sklearn.ensemble import RandomForestRegressor, ExtraTreesRegressor
from sklearn.ensemble import AdaBoostRegressor, GradientBoostingRegressor

import warnings

# State Level Models

In [2]:
state_data = pd.read_csv('../Data/merged_state_final.csv')
state_data.head()

Location  Employment_2020  Employment_2021  Employment_2022  \
0     Alabama          2671005          2769464          2869931   
1      Alaska           430840           443047           457687   
2     Arizona          3920033          4086802          4287595   
3    Arkansas          1639829          1686444          1755536   
4  California         23154091         23934549         25300974   

   Inc_Per_Cap_2020  Inc_Per_Cap_2021  Inc_Per_CAp_2022  Life_Exp_2020  \
0             45887             50059             50916           73.2   
1             61898             65662             68635           76.6   
2             52133             56420             58442           76.3   
3             47147             51636             52618           73.8   
4             70061             76991             77036           79.0   

   Life_Exp_2019  Life_Exp_2018  ...  Yes, 50 or more people  all_causes_2020  \
0           75.2           75.1  ...                    1.00             9021   
1           77.7           78.0  ...                    0.00              545   
2           78.8           78.7  ...                    2.89            13186   
3           75.7           75.6  ...                    1.00             4992   
4           80.9           80.8  ...                    1.18            41279   

   all_causes_2021  all_causes_2022  covid_2020  covid_2021  covid_2022  \
0            13018             6246        6337        9771        3933   
1             1429              686         213         804         275   
2            17961             8835        8603       13536        5849   
3             6908             3854        3691        5333        2593   
4            60680            36786       29962       48834       21158   

   Covid_pop_perce_2020  Covid_pop_perce_2021  Covid_pop_perce_2022  
0              0.001261              0.001945              0.000783  
1              0.000290              0.001096              0.000375  
2              0.001203              0.001893              0.000818  
3              0.001226              0.001771              0.000861  
4              0.000758              0.001235              0.000535  

[5 rows x 123 columns]

## Y = Excess Deaths

In [3]:
X1 = state_data.drop(columns=['Location', 'Mask_Mandate','Exc_deaths_2017', 'Exc_deaths_2018','Exc_deaths_2019',
                              'Exc_deaths_2020', 'Exc_deaths_2021','Exc_deaths_2022',
                      'all_causes_2020', 'all_causes_2021', 'all_causes_2022', 'covid_2020',
                      'covid_2021', 'covid_2022', 'Covid_pop_perce_2020', 'Covid_pop_perce_2021',
                     'Covid_pop_perce_2022'])
y1 = state_data[['Exc_deaths_2020', 'Exc_deaths_2021','Exc_deaths_2022']]

In [4]:
X1_train, X1_test, y1_train, y1_test = train_test_split(X1, y1, random_state=42)

#### Model 1 - Random Forest with Standard Scaler

In [5]:
state_sc = StandardScaler()
X1_train_sc = state_sc.fit_transform(X1_train)
X1_test_sc = state_sc.transform(X1_test)

In [6]:
state_rf1 = RandomForestRegressor()
state_rf1.fit(X1_train, y1_train)
state_rf1.score(X1_train, y1_train), state_rf1.score(X1_test, y1_test)

(0.9446593525509764, 0.6911742373599838)

#### Model 2 - Random Forest with Poly and Standard Scaler

In [7]:
state_poly1 = PolynomialFeatures()
X1_train_poly = state_poly1.fit_transform(X1_train)
X1_test_poly = state_poly1.transform(X1_test)

state_sc1 = StandardScaler()
X1_train_polysc = state_sc1.fit_transform(X1_train_poly)
X1_test_polysc = state_sc1.transform(X1_test_poly)

In [8]:
state_rf2 = RandomForestRegressor()
state_rf2.fit(X1_train_polysc, y1_train)
state_rf2.score(X1_train_polysc, y1_train), state_rf2.score(X1_test_polysc, y1_test)

(0.9481181550973048, 0.719390441418474)

#### Model 3 - GradBoosting, MultiOutput & GridSearch with Poly & Standard Scaler

In [9]:
grad = GradientBoostingRegressor()
multi1 = MultiOutputRegressor(grad)

pgrid = {
    'estimator__learning_rate': [0.1, 1, 10],
    'estimator__n_estimators': [10, 100],
    'estimator__max_depth': [None, 1, 2, 3]
}

kf1 = KFold(n_splits=10, shuffle=True, random_state=42)
gs1 = GridSearchCV(multi1, pgrid, cv=kf1, n_jobs=-1)

In [10]:
%%time
gs1.fit(X1_train_polysc, y1_train)

/Users/anaconda3/lib/python3.11/site-packages/sklearn/model_selection/_search.py:987: RuntimeWarning: overflow encountered in square
  (array - array_means[:, np.newaxis]) ** 2, axis=1, weights=weights


CPU times: user 7.52 s, sys: 117 ms, total: 7.64 s
Wall time: 2min 43s


GridSearchCV(cv=KFold(n_splits=10, random_state=42, shuffle=True),
             estimator=MultiOutputRegressor(estimator=GradientBoostingRegressor()),
             n_jobs=-1,
             param_grid={'estimator__learning_rate': [0.1, 1, 10],
                         'estimator__max_depth': [None, 1, 2, 3],
                         'estimator__n_estimators': [10, 100]})

In [11]:
gs1.score(X1_train_polysc, y1_train), gs1.score(X1_test_polysc, y1_test)

(0.9999989358913751, 0.6818274094030404)

## Y = Covid Deaths

In [12]:
X2 = state_data.drop(columns=['Location', 'Mask_Mandate','Exc_deaths_2017', 'Exc_deaths_2018','Exc_deaths_2019',
                              'Exc_deaths_2020', 'Exc_deaths_2021','Exc_deaths_2022',
                      'all_causes_2020', 'all_causes_2021', 'all_causes_2022', 'covid_2020',
                      'covid_2021', 'covid_2022', 'Covid_pop_perce_2020', 'Covid_pop_perce_2021',
                     'Covid_pop_perce_2022'])
y2 = state_data[['covid_2020', 'covid_2021', 'covid_2022']]

In [13]:
X2_train, X2_test, y2_train, y2_test = train_test_split(X2, y2, random_state=42)

In [14]:
state_poly2 = PolynomialFeatures()
X2_trainpoly = state_poly2.fit_transform(X2_train)
X2_testpoly = state_poly2.transform(X2_test)

state_ss2 = StandardScaler()
X2_train_polysc = state_ss2.fit_transform(X2_trainpoly)
X2_test_polysc = state_ss2.transform(X2_testpoly)

#### Model 1 - Random Forest with Poly & Standard Scaler

In [15]:
state_rf3 = RandomForestRegressor()
state_rf3.fit(X2_train_polysc, y2_train)
state_rf3.score(X2_train_polysc, y2_train), state_rf3.score(X2_test_polysc, y2_test)

(0.9507527562189915, 0.7175893573091306)

#### Model 2 - KNN with Poly & Standard Scaler

In [16]:
state_knn = KNeighborsRegressor()
state_knn.fit(X2_train_polysc, y2_train)
state_knn.score(X2_train_polysc, y2_train), state_knn.score(X2_test_polysc, y2_test)

(0.7436503805578066, 0.5625614945672842)

#### Model 3 - GradBoost, MultiOutput & GridSearch with Poly & Standard Scaler

In [17]:
warnings.filterwarnings("ignore", category=RuntimeWarning)

grad = GradientBoostingRegressor()
multi2 = MultiOutputRegressor(grad)

pgrid = {
    'estimator__learning_rate': [0.1, 1, 10],
    'estimator__n_estimators': [10, 100, 200, 300],
    'estimator__max_depth': [None, 1, 2, 3]
}

kf1 = KFold(n_splits=10, shuffle=True, random_state=42)
gs2 = GridSearchCV(multi2, pgrid, cv=kf1, n_jobs=-1)

In [18]:
%%time
with warnings.catch_warnings():
    warnings.simplefilter("ignore")
    gs2.fit(X2_train_polysc, y2_train)

/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/numpy/core/fromnumeric.py:86: RuntimeWarning: overflow encountered in reduce
  return ufunc.reduce(obj, axis, dtype, out, **passkwargs)
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/numpy/core/fromnumeric.py:86: RuntimeWarning: overflow encountered in reduce
  return ufunc.reduce(obj, axis, dtype, out, **passkwargs)
/Users/anaconda3/lib/python3.11/site-packages/sklearn/ensemble/_gb_losses.py:229: RuntimeWarning: overflow encountered in square
  * np.sum(sample_weight * ((y - raw_predictions.ravel()) ** 2))
/Users/anaconda3/lib/python3.11/site-packages/numpy/co

CPU times: user 13.5 s, sys: 1.03 s, total: 14.5 s
Wall time: 15min 11s


In [19]:
gs2.score(X2_train_polysc, y2_train), gs2.score(X2_test_polysc, y2_test)

(0.9999995775587474, 0.9030538450073794)

In [20]:
gs2.best_params_

{'estimator__learning_rate': 0.1,
 'estimator__max_depth': 1,
 'estimator__n_estimators': 300}

#### Model 4 -  Random Forest, KFold & GridSearch with Poly & Standard Scaler

In [21]:
params = {
    'max_features': np.arange(1, X2.shape[1] + 1), 
    'max_depth': np.append(np.arange(1, 10), None), 
    'min_samples_leaf': np.arange(1, 31) 
}
kf = KFold(n_splits=10, shuffle=True, random_state=2023)
ranfor = RandomForestRegressor(
    n_estimators=100,
    random_state=2023
)

gs2 = GridSearchCV(ranfor, params, cv=kf, n_jobs=-1)

In [22]:
%%time
gs2.fit(X2_train_polysc, y2_train)

CPU times: user 1min 43s, sys: 15.7 s, total: 1min 59s
Wall time: 37min 58s


GridSearchCV(cv=KFold(n_splits=10, random_state=2023, shuffle=True),
             estimator=RandomForestRegressor(random_state=2023), n_jobs=-1,
             param_grid={'max_depth': array([1, 2, 3, 4, 5, 6, 7, 8, 9, None], dtype=object),
                         'max_features': array([  1,   2,   3,   4,   5,   6,   7,   8,   9,  10,  11,  12,  13,
        14,  15,  16,  17,  18,  19,  20,  21,  22,  23,  24,  25,  26,
        27,  28,  29,  30,  31,  32,  33,  34,  35,  36,  37,  38,  39,
        40,  41,  42,  43,  44,  45,  46,  47,  48,  49,  50,  51,  52,
        53,  54,  55,  56,  57,  58,  59,  60,  61,  62,  63,  64,  65,
        66,  67,  68,  69,  70,  71,  72,  73,  74,  75,  76,  77,  78,
        79,  80,  81,  82,  83,  84,  85,  86,  87,  88,  89,  90,  91,
        92,  93,  94,  95,  96,  97,  98,  99, 100, 101, 102, 103, 104,
       105, 106]),
                         'min_samples_leaf': array([ 1,  2,  3,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 15, 16, 17,
       18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30])})

In [23]:
gs2.score(X2_train_polysc, y2_train), gs2.score(X2_test_polysc, y2_test)

(0.7930247825616247, 0.6592708754598661)

#### Model 5 - LASSO  Model

In [24]:
las = Lasso(max_iter=1000, alpha=0.1)
las.fit(X2_train, y2_train)
las.score(X2_train, y2_train), las.score(X2_test, y2_test)

(0.9999991400245168, 0.9226665134912698)

# County Level Data

In [25]:
county_data = pd.read_csv('../Data/Cleaned/county_df3.csv')
county_data.head()

FIPS_x  Years of Potential Life Lost Rate (premature death)  \
0    1001                                             8824.0     
1    1003                                             7225.0     
2    1005                                             9586.0     
3    1007                                            11784.0     
4    1009                                            10908.0     

   % Fair/Poor Health  percent_smokers  percent_obese  Food Environment Index  \
0                  18               19             38                     7.2   
1                  18               17             31                     8.0   
2                  26               22             44                     5.6   
3                  20               20             38                     7.6   
4                  21               20             34                     8.5   

   % Physically Inactive  percent Excessive Drinking  PCP Rate  \
0                     31                          17      42.0   
1                     24                          17      73.0   
2                     28                          13      39.0   
3                     35                          16      57.0   
4                     29                          15      23.0   

   Preventable Hosp stays Rate  ...  percent Non-Hispanic White  \
0                       6599.0  ...                        74.5   
1                       3833.0  ...                        83.0   
2                       4736.0  ...                        46.0   
3                       5998.0  ...                        74.3   
4                       4162.0  ...                        86.9   

   percent Not Proficient in English  percent Female  number Rural  Masks  \
0                                  1            51.3       22921.0  267.0   
1                                  0            51.5       77060.0  267.0   
2                                  1            47.2       18613.0  267.0   
3                                  0            46.5       15663.0  267.0   
4                                  2            50.7       51562.0  267.0   

   Administered_Dose1_Pop_Pct  Administered_Dose1_Recip_65PlusPop_Pct  water  \
0                        42.2                                    73.8      0   
1                        53.2                                    89.9      1   
2                        44.5                                    75.3      0   
3                        36.6                                    64.2      0   
4                        31.9                                    56.6      0   

     cases  deaths  
0  18961.0   230.0  
1  67496.0   719.0  
2   7027.0   103.0  
3   7692.0   108.0  
4  17731.0   260.0  

[5 rows x 48 columns]

## Y = Number of Cases

#### Model 1 - 8 X Variables

In [26]:
y3 = county_data['cases']
X3 = county_data[['% Physically Inactive', 'Percent Unemployed', 'Average Daily PM2.5', 'Percent Insufficient Sleep', 'Percent Uninsured Adults',
       'Population', 'percent Asian', 'percent Not Proficient in English', 'Masks', 'Administered_Dose1_Pop_Pct']]

# TTS
X3_train, X3_test, y3_train, y3_test = train_test_split(X3, y3, random_state = 42)

In [28]:
lr_county_cases_lim = LinearRegression()
lr_county_cases_lim.fit(X3_train, y3_train)

print(f'Train Score: {lr_county_cases_lim.score(X3_train, y3_train)}')
print(f'Test Score: {lr_county_cases_lim.score(X3_test, y3_test)}')

Train Score: 0.9639786858046525
Test Score: 0.9325020606715091


In [29]:
pd.DataFrame(set(zip(X3.columns, lr_county_cases_lim.coef_)), columns = ['Variable Name',
                                'Coefficient']).sort_values('Coefficient').round(1).head(5)

Variable Name  Coefficient
3             percent Asian      -2293.4
7       Average Daily PM2.5      -1333.1
9        Percent Unemployed      -1221.3
8  Percent Uninsured Adults       -401.5
5                     Masks         -3.8

#### Random Forest (RF) w/ GradBoost & Random Search CV

In [30]:
y4 = county_data['cases']
X4 = county_data.drop(columns = ['cases', 'deaths'])

# TTS
X4_train, X4_test, y4_train, y4_test = train_test_split(X4, y4, random_state = 42)

In [32]:
params = {
    'max_features': np.arange(5, X4.shape[1] + 1),
    'max_depth': np.append(np.arange(1, 50), None),
    'min_samples_leaf': [2, 3],   
    'n_estimators': [50, 100, 200, 400, 600, 800, 1000, 1200, 1400, 1600, 1800, 2000]
}

rf_gb = GradientBoostingRegressor(random_state = 42)

rf_gb_county_cases = RandomizedSearchCV(rf_gb, params, n_iter=100, cv = 5, n_jobs = -1)

In [33]:
%%time
rf_gb_county_cases.fit(X4_train, y4_train)

CPU times: user 1.71 s, sys: 372 ms, total: 2.08 s
Wall time: 22min 32s


RandomizedSearchCV(cv=5, estimator=GradientBoostingRegressor(random_state=42),
                   n_iter=100, n_jobs=-1,
                   param_distributions={'max_depth': array([1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19,
       20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36,
       37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, None],
      dtype=object),
                                        'max_features': array([ 5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21,
       22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38,
       39, 40, 41, 42, 43, 44, 45, 46]),
                                        'min_samples_leaf': [2, 3],
                                        'n_estimators': [50, 100, 200, 400, 600,
                                                         800, 1000, 1200, 1400,
                                                         1600, 1800, 2000]})

In [34]:
print(f'Train Score: {rf_gb_county_cases.score(X4_train, y4_train)}')
print(f'Test Score: {rf_gb_county_cases.score(X4_test, y4_test)}')

Train Score: 0.9639525971632665
Test Score: 0.8854569972674492


In [35]:
rf_gb_county_cases.best_params_

{'n_estimators': 50,
 'min_samples_leaf': 3,
 'max_features': 24,
 'max_depth': 32}

In [37]:
pd.DataFrame({'Features': X4.columns, 'Importance': rf_gb_county_cases.best_estimator_. \
              feature_importances_}).sort_values('Importance', ascending = False).head(10)

Features  Importance
30                                      Population    0.681771
16                 Percent Severe Housing Problems    0.100550
35                                   percent Asian    0.060275
17                      Severe Housing Cost Burden    0.030048
15                             Average Daily PM2.5    0.023543
36  percent Native Hawaiian/Other Pacific Islander    0.014046
43                      Administered_Dose1_Pop_Pct    0.012845
23                           Percent Food Insecure    0.007891
39               percent Not Proficient in English    0.007504
3                                  percent_smokers    0.006320

#### Extra Trees (ET) w/ Random Search CV

In [38]:
params = {
    'max_features': np.arange(5, X4.shape[1] + 1),
    'min_samples_leaf': [2, 3],
    'max_depth': [None, 10, 20, 30, 40, 50],
    'n_estimators': [50, 100, 200, 400, 600, 800, 1000, 1200, 1400, 1600, 1800, 2000]
}

et = ExtraTreesRegressor(n_estimators = 500, random_state = 42)

et_rs_county_cases = RandomizedSearchCV(et, params, n_iter=100, cv = 5, n_jobs = -1)

In [39]:
%%time
et_rs_county_cases.fit(X4_train, y4_train)

CPU times: user 10.1 s, sys: 404 ms, total: 10.5 s
Wall time: 3min 29s


RandomizedSearchCV(cv=5,
                   estimator=ExtraTreesRegressor(n_estimators=500,
                                                 random_state=42),
                   n_iter=100, n_jobs=-1,
                   param_distributions={'max_depth': [None, 10, 20, 30, 40, 50],
                                        'max_features': array([ 5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21,
       22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38,
       39, 40, 41, 42, 43, 44, 45, 46]),
                                        'min_samples_leaf': [2, 3],
                                        'n_estimators': [50, 100, 200, 400, 600,
                                                         800, 1000, 1200, 1400,
                                                         1600, 1800, 2000]})

In [40]:
print(f'Train Score: {et_rs_county_cases.score(X4_train, y4_train)}')
print(f'Test Score: {et_rs_county_cases.score(X4_test, y4_test)}')

Train Score: 0.9020260820524172
Test Score: 0.9037012483227174


In [41]:
et_rs_county_cases.best_params_

{'n_estimators': 1600,
 'min_samples_leaf': 2,
 'max_features': 46,
 'max_depth': 50}

In [42]:
pd.DataFrame({'Features': X4.columns, 'Importance': et_rs_county_cases.best_estimator_. \
              feature_importances_}).sort_values('Importance', ascending = False).head(10)

Features  Importance
30                         Population    0.696555
35                      percent Asian    0.059111
16    Percent Severe Housing Problems    0.055516
17         Severe Housing Cost Burden    0.023603
39  percent Not Proficient in English    0.017054
15                Average Daily PM2.5    0.016344
18                       Overcrowding    0.015868
14                       Income Ratio    0.009930
41                       number Rural    0.008088
3                     percent_smokers    0.007042

## Y = Deaths

#### Model 1 - 8 X-Variables

In [43]:
y5 = county_data['deaths']
X5 = county_data[['% Physically Inactive', 'Percent Unemployed', 'Average Daily PM2.5',
                  'Percent Insufficient Sleep', 'Percent Uninsured Adults','Population',
                  'percent Asian', 'percent Not Proficient in English', 'Masks',
                  'Administered_Dose1_Pop_Pct']]

# TTS
X5_train, X5_test, y5_train, y5_test = train_test_split(X5, y5, random_state = 42)

In [44]:
lr_county_deaths_lim = LinearRegression()
lr_county_deaths_lim.fit(X5_train, y5_train)

print(f'Train Score: {lr_county_deaths_lim.score(X5_train, y5_train)}')
print(f'Test Score: {lr_county_deaths_lim.score(X5_test, y5_test)}')

Train Score: 0.9234030729783924
Test Score: 0.9044371813655546


In [45]:
pd.DataFrame(set(zip(X5.columns, lr_county_deaths_lim.coef_)), columns = ['Variable Name', \
                                'Coefficient']).sort_values('Coefficient').round(1).head(5)

Variable Name  Coefficient
5               percent Asian        -41.2
9         Average Daily PM2.5        -19.5
6    Percent Uninsured Adults         -5.4
4          Percent Unemployed         -3.6
7  Administered_Dose1_Pop_Pct         -0.2

#### Model 2 - Random Forest (RF) w/ GradBoost & Random Search CV

In [46]:
y6 = county_data['deaths']
X6 = county_data.drop(columns = ['cases', 'deaths'])

# TTS
X6_train, X6_test, y6_train, y6_test = train_test_split(X6, y6, random_state = 42)

In [48]:
params = {
    'max_features': np.arange(5, X6.shape[1] + 1),
    'max_depth': np.append(np.arange(1, 50), None),
    'n_estimators': [50, 100, 150, 200, 250, 300, 350, 400, 450, 500]
}

rf_gb = GradientBoostingRegressor(random_state = 42)

rf_gb_county_deaths = RandomizedSearchCV(rf_gb, params, n_iter=100, cv = 5, n_jobs = -1)

In [49]:
%%time
rf_gb_county_deaths.fit(X6_train, y6_train)

CPU times: user 1.17 s, sys: 279 ms, total: 1.44 s
Wall time: 4min 21s


RandomizedSearchCV(cv=5, estimator=GradientBoostingRegressor(random_state=42),
                   n_iter=100, n_jobs=-1,
                   param_distributions={'max_depth': array([1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19,
       20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36,
       37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, None],
      dtype=object),
                                        'max_features': array([ 5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21,
       22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38,
       39, 40, 41, 42, 43, 44, 45, 46]),
                                        'n_estimators': [50, 100, 150, 200, 250,
                                                         300, 350, 400, 450,
                                                         500]})

In [50]:
print(f'Train Score: {rf_gb_county_deaths.score(X6_train, y6_train)}')
print(f'Test Score: {rf_gb_county_deaths.score(X6_test, y6_test)}')

Train Score: 0.9779164247902902
Test Score: 0.8888458905787248


In [51]:
rf_gb_county_deaths.best_params_

{'n_estimators': 350, 'max_features': 28, 'max_depth': 1}

In [52]:
pd.DataFrame({'Features': X6.columns, 'Importance': rf_gb_county_deaths.best_estimator_.\
              feature_importances_}).sort_values('Importance', ascending = False).head(10)

Features  Importance
30                          Population    0.797939
16     Percent Severe Housing Problems    0.101779
15                 Average Daily PM2.5    0.039292
35                       percent Asian    0.038046
17          Severe Housing Cost Burden    0.004704
6                % Physically Inactive    0.003716
29  Segregation Index non-white/ white    0.002330
41                        number Rural    0.001802
5               Food Environment Index    0.001609
12                Percent Some College    0.001595